<a href="https://colab.research.google.com/github/OritPa/ML_TripAdvisor_Pipeline/blob/main/Feature_Engineering.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [5]:
!pip install scikit-learn --quiet
!pip install pygeohash --quiet
!pip -q install folium --quiet


In [6]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import pickle
import string
import re
import ast
warnings.filterwarnings("ignore")
%matplotlib inline
from sklearn.neighbors import BallTree
import pygeohash as pgh
import folium
from folium.plugins import MarkerCluster
from datetime import datetime, timedelta

# DATA ENGINEERING

###Uploading the data

In [7]:
# Data AFTER outlier
with open('df_after_outliers.pkl', 'rb') as file:
    df = pickle.load(file)

In [8]:
#Original data saved columns for feature engineering
with open('df_saved_columns.pkl', 'rb') as file:
    df_saved_columns = pickle.load(file)


In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224763 entries, 0 to 224762
Data columns (total 63 columns):
 #   Column                             Non-Null Count   Dtype   
---  ------                             --------------   -----   
 0   restaurant_link                    224763 non-null  string  
 1   restaurant_name                    224763 non-null  string  
 2   region                             224763 non-null  string  
 3   province                           224763 non-null  string  
 4   city                               224763 non-null  string  
 5   address                            224763 non-null  string  
 6   latitude                           224763 non-null  float64 
 7   longitude                          224763 non-null  float64 
 8   claimed                            224763 non-null  int64   
 9   awards                             224763 non-null  int64   
 10  popularity_detailed                224763 non-null  string  
 11  popularity_generic        

In [10]:
df_saved_columns.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224763 entries, 0 to 224762
Data columns (total 11 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   restaurant_link           224763 non-null  string
 1   restaurant_name           224763 non-null  string
 2   top_tags                  224763 non-null  string
 3   province_before_grouping  202503 non-null  string
 4   city_before_grouping      224763 non-null  string
 5   region_before_grouping    224763 non-null  string
 6   meals                     224763 non-null  string
 7   cuisines                  224763 non-null  string
 8   features                  70162 non-null   object
 9   original_open_hours       118266 non-null  object
 10  keywords                  5566 non-null    object
dtypes: object(3), string(8)
memory usage: 18.9+ MB


##Columns to be dropped after engineering

In [11]:
# -------- 1) Static sets (intent-based) --------
RATING_COLS  = ["excellent","very_good","average","poor","terrible"]
EXP_COLS     = ["food","service","value","atmosphere"]
LEAKAGE_COLS = RATING_COLS + EXP_COLS + [
    "avg_rating",
    "total_reviews_count",
    "reviews_count_in_default_language"
]

# Keep cuisines__* ; drop top_tags__* counterparts
DUPLICATE_SEMANTICS_DROP = [
    "top_tags__italian","top_tags__pizza","top_tags__seafood","top_tags__mediterranean"
]

# IDs / non-predictive text fields
ID_LIKE_COLS = [
    "restaurant_link","restaurant_name","address"
]

# Known temporary / provenance columns to exclude from modeling
TEMP_TECH_COLS = [
   "cuisines", "longitude", "latitude", "special_diets", 'popularity_detailed',  'popularity_generic'
]

##Location-based features

In [12]:
POP_RADIUS_M = 800
EARTH_RADIUS_M = 6_371_000.0
ATTR_PERCENTILE = 95

def compute_offline_scores(df, lat_col="latitude", lon_col="longitude"):
    out = df.copy()
    mask = out[lat_col].notna() & out[lon_col].notna()
    if not mask.any():
        out["area_popularity_raw"] = 0
        out["area_popularity_0_100"] = 0.0
        out["is_tourist_attraction"] = 0
        return out

    coords_rad = np.radians(out.loc[mask, [lat_col, lon_col]].to_numpy(float))
    tree = BallTree(coords_rad, metric="haversine")
    r_rad = POP_RADIUS_M / EARTH_RADIUS_M
    # subtract self
    counts = tree.query_radius(coords_rad, r=r_rad, count_only=True).astype(int) - 1

    # 0–100 scale
    if counts.max() > counts.min():
        scaled = (counts - counts.min()) / (counts.max() - counts.min()) * 100
    else:
        scaled = np.zeros_like(counts, dtype=float)

    thr = np.quantile(counts, ATTR_PERCENTILE/100.0)
    flag = (counts >= thr).astype(int)

    out.loc[mask, "area_popularity_raw"] = counts
    out.loc[mask, "area_popularity_0_100"] = scaled.round(1)
    out.loc[mask, "is_tourist_attraction"] = flag
    out.loc[~mask, ["area_popularity_raw","area_popularity_0_100","is_tourist_attraction"]] = [0,0.0,0]
    return out

df = compute_offline_scores(df, "latitude", "longitude")


In [13]:
# --- Use original city  ---
# df_saved_columns = df_italy[saved_columns]
df = df.merge(
    df_saved_columns[["restaurant_link","city_before_grouping","province_before_grouping","region_before_grouping"]],
    on="restaurant_link", how="left"
)
df["city_for_distance"] = df["city_before_grouping"].fillna(df["city"])

# --- City centers from original city name ---
centers = (
    df.groupby("city_for_distance")[["latitude","longitude"]]
      .mean()
      .rename(columns={"latitude":"center_lat","longitude":"center_lon"})
)

df = df.merge(centers, on="city_for_distance", how="left")

# --- Vectorized Haversine  ---
EARTH_RADIUS_M = 6_371_000.0
lat1 = np.radians(df["latitude"])
lon1 = np.radians(df["longitude"])
lat2 = np.radians(df["center_lat"])
lon2 = np.radians(df["center_lon"])
dlon = lon2 - lon1
dlat = lat2 - lat1
a = np.sin(dlat/2)**2 + np.cos(lat1)*np.cos(lat2)*np.sin(dlon/2)**2
df["distance_to_city_center_m"] = EARTH_RADIUS_M * 2 * np.arcsin(np.sqrt(a))

# cleanup temporary center columns (but KEEP the distance)
df = df.drop(columns=["center_lat","center_lon","city_before_grouping", "province_before_grouping", "city_for_distance" ])


In [14]:
#Num of values in consolidated region
df["restaurant_density_total_region"] = df.groupby("region")["region"].transform("size")

In [15]:
df["restaurant_density_total_region"].value_counts()

restaurant_density_total_region
105625    105625
57752      57752
38766      38766
22620      22620
Name: count, dtype: int64

In [16]:
#Num of values in pre-altered region
df["restaurant_density_original_region"] = df.groupby("region_before_grouping")["region_before_grouping"].transform("size")

In [17]:
df["restaurant_density_original_region"].value_counts()

restaurant_density_original_region
33097    33097
23831    23831
18861    18861
17823    17823
17569    17569
17568    17568
16330    16330
15701    15701
12452    12452
8971      8971
6919      6919
6027      6027
6006      6006
5968      5968
5538      5538
4657      4657
3516      3516
1704      1704
1211      1211
1014      1014
Name: count, dtype: int64

In [18]:
df = df.drop(columns=['region_before_grouping'])

In [19]:
# Text flags from address (foot-traffic proxies; tweak keywords as needed)
kw = r"(piazza|stazione|station|airport|aeroporto|marina|porto|harbor|mall|centro|centro storico|old town|hotel)"
df["addr_foot_traffic_flag"] = df["address"].str.contains(kw, case=False, na=False).astype(int)

In [20]:
df["addr_foot_traffic_flag"].value_counts()

addr_foot_traffic_flag
0    192707
1     32056
Name: count, dtype: int64

In [21]:
#Due to high cardinality of popularity_detailed and lack of standardization, will extract only rank and num of restarants per location
pattern = r'(\d+)\s*of\s*(\d+)'

df[['popularity_rank', 'num_restaurants_per_city']] = (
    df['popularity_detailed']
    .str.extract(pattern)
    .astype('Int64')
)

df['popularity_rank'] = df['popularity_rank'].astype('Int64').fillna(0)
df['num_restaurants_per_city'] = df['num_restaurants_per_city'].astype('Int64').fillna(0)

In [22]:
df[['popularity_detailed','popularity_rank', 'num_restaurants_per_city']].head()

popularity_detailed  popularity_rank  \
0        1 of 1 Restaurant in Vito d Asio                1   
1                                 Unknown                0   
2      1 of 1 Restaurant in San Francesco                1   
3  1 of 1 Restaurant in Valdaora di Sopra                1   
4        5 of 5 Restaurants in Toscanella                5   

   num_restaurants_per_city  
0                         1  
1                         0  
2                         1  
3                         1  
4                         5

In [23]:
df["popularity_rank"] = df["popularity_rank"].astype("Int64")
df["num_restaurants_per_city"] = df["num_restaurants_per_city"].astype("Int64")

den = df["num_restaurants_per_city"].replace({0: pd.NA})
df["relative_popularity_rank"] = (df["popularity_rank"] / den).astype("Float64").fillna(0)

In [24]:
df["relative_popularity_rank"].isna().sum()

np.int64(0)

In [25]:
# “City size buckets” (based on restaurant_count)
q = df["num_restaurants_per_city"].quantile([0.33, 0.66]).to_list()
def bucket(n):
    if pd.isna(n): return "unknown"
    if n <= q[0]:  return "small"
    if n <= q[1]:  return "medium"
    return "large"
df["city_size_bucket"] = df["num_restaurants_per_city"].apply(bucket).astype("category")

In [26]:
df["city_size_bucket"].value_counts()

city_size_bucket
large     76409
small     75105
medium    73249
Name: count, dtype: int64

##Country map

In [27]:
def in_italy_bbox(lat, lon):
    """Return True if (lat, lon) falls inside mainland Italy or major islands."""
    # mainland
    mainland = (35.4 <= lat <= 47.4) and (6.2 <= lon <= 18.9)
    # sicily
    sicily   = (36.3 <= lat <= 38.8) and (12.3 <= lon <= 15.7)
    # sardinia
    sardinia = (38.7 <= lat <= 41.4) and (8.0  <= lon <= 9.9)
    return mainland or sicily or sardinia

def apply_italy_filter(df, lat_col="latitude", lon_col="longitude", mode="null"):
    """
    mode = 'null' → set coords to NaN if outside Italy
    mode = 'drop' → drop rows outside Italy
    Adds a boolean column `is_in_italy_bbox`.
    """
    mask_valid = df[lat_col].notna() & df[lon_col].notna()
    mask_in = np.zeros(len(df), dtype=bool)
    mask_in[mask_valid.values] = [
        in_italy_bbox(la, lo) for la, lo in zip(df.loc[mask_valid, lat_col], df.loc[mask_valid, lon_col])
    ]
    out = df.copy()
    out["is_in_italy_bbox"] = mask_in.astype(int)

    if mode == "drop":
        out = out[out["is_in_italy_bbox"].eq(1)].copy()
    else:  # 'null'
        out.loc[out["is_in_italy_bbox"].eq(0), [lat_col, lon_col]] = np.nan

    return out


In [28]:
def plot_restaurants_map(df_map, lat_col="latitude", lon_col="longitude",
                         color_by="target", sample_max=5000, start=(41.9, 12.5), zoom=5):
    """
    color_by can be 'target', 'is_michelin', 'is_in_italy_bbox', or None.
    """
    data = df_map.dropna(subset=[lat_col, lon_col]).copy()
    if len(data) > sample_max:
        data = data.sample(sample_max, random_state=42)

    def pick_color(row):
        if color_by is None:
            return "blue"
        val = row.get(color_by, 0)
        try:
            val = int(val)
        except Exception:
            pass
        # simple scheme
        if color_by in ("target", "is_michelin", "is_in_italy_bbox"):
            return "red" if val == 1 else "blue"
        return "blue"

    m = folium.Map(location=start, zoom_start=zoom, tiles="CartoDB positron")
    cluster = MarkerCluster().add_to(m)

    # you can customize popup fields
    popup_cols = [c for c in ["restaurant_name", "city", "region", "target", "is_michelin"] if c in data.columns]

    for _, r in data.iterrows():
        popup_txt = " | ".join([f"{c}: {r.get(c, '')}" for c in popup_cols]) if popup_cols else ""
        folium.CircleMarker(
            location=(r[lat_col], r[lon_col]),
            radius=2.5,
            color=pick_color(r),
            fill=True,
            fill_opacity=0.8,
            popup=popup_txt if popup_txt else None,
        ).add_to(cluster)

    return m




In [29]:
# Example usage after cleaning:
df_clean = apply_italy_filter(df, mode="null")
m = plot_restaurants_map(df_clean, color_by="target")  # or "is_michelin" / "is_in_italy_bbox"
m  # shows inline in Colab
#m.save("restaurants_map.html")

In [30]:
# How many points got nulled/dropped?
df_clean = apply_italy_filter(df, mode="null")
print("Inside Italy bbox:", int(df_clean["is_in_italy_bbox"].sum()))
print("Outside bbox (coords set to NaN):", int((df_clean["is_in_italy_bbox"]==0).sum()))
print("Rows with coordinates present:", df_clean[["latitude","longitude"]].notna().all(axis=1).sum())


Inside Italy bbox: 224617
Outside bbox (coords set to NaN): 146
Rows with coordinates present: 224617


##Restaurant- based features

In [31]:
#If restaurant name appears more than once then it is most likely part of a chain
df['is_restaurant_chain'] = (df.groupby('restaurant_name')['restaurant_name']
                        .transform('size') > 1).astype(int)

In [32]:
df['is_restaurant_chain'].value_counts()

is_restaurant_chain
0    170545
1     54218
Name: count, dtype: int64

In [33]:
# If a restaurant caters to all three major dietary restrictions, flag it as 1.
df['is_full_diet_friendly'] = np.where(
    (df['gluten_free'] == 1) &
    (df['vegan_options'] == 1) &
    (df['vegetarian_friendly'] == 1),
    1,
    0
)

In [34]:
df['is_full_diet_friendly'].value_counts()

is_full_diet_friendly
0    209951
1     14812
Name: count, dtype: int64

In [35]:
df_saved_columns['original_open_hours'].value_counts()

original_open_hours
{"Mon": ["00:00-23:59"], "Tue": ["00:00-23:59"], "Wed": ["00:00-23:59"], "Thu": ["00:00-23:59"], "Fri": ["00:00-23:59"], "Sat": ["00:00-23:59"], "Sun": ["00:00-23:59"]}                                                                                                             2386
{"Mon": ["12:00-15:00", "19:00-00:00"], "Tue": ["12:00-15:00", "19:00-00:00"], "Wed": ["12:00-15:00", "19:00-00:00"], "Thu": ["12:00-15:00", "19:00-00:00"], "Fri": ["12:00-15:00", "19:00-00:00"], "Sat": ["12:00-15:00", "19:00-00:00"], "Sun": ["12:00-15:00", "19:00-00:00"]}     473
{"Mon": ["12:00-15:00", "19:00-23:00"], "Tue": ["12:00-15:00", "19:00-23:00"], "Wed": ["12:00-15:00", "19:00-23:00"], "Thu": ["12:00-15:00", "19:00-23:00"], "Fri": ["12:00-15:00", "19:00-23:00"], "Sat": ["12:00-15:00", "19:00-23:00"], "Sun": ["12:00-15:00", "19:00-23:00"]}     466
{"Mon": ["07:00-00:00"], "Tue": ["07:00-00:00"], "Wed": ["07:00-00:00"], "Thu": ["07:00-00:00"], "Fri": ["07:00-00:00"], "Sat": ["07:00-00:00"], "Sun": ["07:00-00:00"]}                                                                                                              434
{"Mon": ["12:00-00:00"], "Tue": ["12:00-00:00"], "Wed": ["12:00-00:00"], "Thu": ["12:00-00:00"], "Fri": ["12:00-00:00"], "Sat": ["12:00-00:00"], "Sun": ["12:00-00:00"]}                                                                                                              414
                                                                                                                                                                                                                                                                                     ... 
{"Mon": ["17:00-20:00"], "Tue": ["11:00-14:30", "17:00-20:00"], "Wed": ["11:00-14:30", "17:00-20:00"], "Thu": ["11:00-14:30", "17:00-20:00"], "Fri": ["11:00-14:30", "17:00-20:00"], "Sat": [], "Sun": []}                                                                              1
{"Mon": ["12:00-14:30", "18:00-00:00"], "Tue": ["12:00-14:30", "18:00-00:00"], "Wed": ["12:00-14:30", "18:00-00:00"], "Thu": ["12:00-14:30", "18:00-00:00"], "Fri": ["12:00-14:30", "18:00-00:00"], "Sat": ["12:00-14:30", "18:00-00:00"], "Sun": ["12:00-14:30"]}                      1
{"Mon": [], "Tue": [], "Wed": [], "Thu": ["09:00-22:30"], "Fri": ["09:00-22:30"], "Sat": ["09:00-23:30"], "Sun": ["09:00-22:30"]}                                                                                                                                                       1
{"Mon": [], "Tue": ["12:00-14:30", "18:30-22:30"], "Wed": ["12:00-14:30", "18:30-22:30"], "Thu": ["12:00-14:30", "18:30-22:30"], "Fri": ["12:00-14:30", "18:30-22:30"], "Sat": ["18:30-22:30"], "Sun": ["12:00-14:30", "18:30-22:30"]}                                                  1
{"Mon": [], "Tue": ["06:00-13:00", "16:00-20:00"], "Wed": ["06:00-13:00", "16:00-20:00"], "Thu": ["06:00-13:00", "16:00-20:00"], "Fri": ["06:00-13:00", "16:00-20:00"], "Sat": ["06:00-13:00", "16:00-20:00"], "Sun": ["06:00-13:00"]}                                                  1
Name: count, Length: 57621, dtype: int64

In [36]:
# ------------------ CONFIG ------------------
ID_COL    = "restaurant_link"
HOURS_COL = "original_open_hours"   # lives in df_saved_columns
DAYS = ["Mon","Tue","Wed","Thu","Fri","Sat","Sun"]

# ------------------ 0) bring hours in (temporarily) ------------------
_added_hours_col = False
if HOURS_COL not in df.columns:
    # make sure needed columns exist in df_saved_columns
    assert {ID_COL, HOURS_COL}.issubset(df_saved_columns.columns), \
        f"Missing {ID_COL} or {HOURS_COL} in df_saved_columns"
    df = df.merge(df_saved_columns[[ID_COL, HOURS_COL]], on=ID_COL, how="left")
    _added_hours_col = True

# ------------------ 1) parse hours -> dict per row ------------------
def parse_hours_cell(x):
    """Return normalized dict {day: [ranges]} or None if unparsable."""
    if pd.isna(x):
        return None
    if isinstance(x, dict):
        d = x
    else:
        s = str(x).strip()
        if not s:
            return None
        try:
            d = ast.literal_eval(s)
        except Exception:
            return None
    out = {}
    for day in DAYS:
        v = d.get(day, [])
        out[day] = v if isinstance(v, list) else []
    return out

df["_hours_dict"] = df[HOURS_COL].apply(parse_hours_cell)

# ------------------ 2) day-open flags ------------------
for day in DAYS:
    df[f"open_{day.lower()}"] = df["_hours_dict"].apply(
        lambda d: int(bool(d and isinstance(d.get(day, []), list) and len(d.get(day, [])) > 0))
    )

# Weekend flag: open on Sat or Sun
df["is_weekend_open_any"] = df[["open_sat", "open_sun"]].max(axis=1).astype(int)
df["is_weekday_open_any"] = df[["open_mon", "open_tue", "open_wed", "open_thu", "open_fri"]].max(axis=1).astype(int)

# ------------------ 3) cleanup temps ------------------
df.drop(columns=["_hours_dict"], inplace=True)
if _added_hours_col:
    # we merged HOURS_COL only for this engineering; remove it now
    df.drop(columns=[HOURS_COL], inplace=True, errors="ignore")


In [37]:
#Calculate shift length based on open_hours_per_week and working_shifts_per_week
df['shift_length_hours']=(df['open_hours_per_week'] / df['working_shifts_per_week']).round(2)

In [38]:
df['shift_length_hours'].value_counts()

shift_length_hours
7.11     106501
10.88     22601
12.69      8783
5.72       7926
3.19       6044
          ...  
9.65          1
14.54         1
8.41          1
3.73          1
11.79         1
Name: count, Length: 777, dtype: int64

In [39]:
#T telationship between michelin and price
df["michelin_x_price"] = df["is_michelin"].astype(float) * df["price_level"].astype(float)

In [40]:
df['michelin_x_price'].value_counts()

michelin_x_price
0.0    222782
3.0      1066
2.0       906
1.0         9
Name: count, dtype: int64

In [41]:
#Final drop
FINAL_DROP=LEAKAGE_COLS+ DUPLICATE_SEMANTICS_DROP+ ID_LIKE_COLS+ TEMP_TECH_COLS+["open_sat", "open_sun","open_mon", "open_tue", "open_wed", "open_thu", "open_fri"]

In [42]:
df = df.drop(columns=FINAL_DROP, errors="ignore")

print(f"✅ Dropped {len(FINAL_DROP)} columns.")
print("Remaining columns:", len(df.columns))

✅ Dropped 32 columns.
Remaining columns: 56


In [43]:
obj_cols = df.select_dtypes(include=["string"]).columns
for col in obj_cols:
  df[col] = df[col].astype("category")

In [44]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224763 entries, 0 to 224762
Data columns (total 56 columns):
 #   Column                              Non-Null Count   Dtype   
---  ------                              --------------   -----   
 0   region                              224763 non-null  category
 1   province                            224763 non-null  category
 2   city                                224763 non-null  category
 3   claimed                             224763 non-null  int64   
 4   awards                              224763 non-null  int64   
 5   price_level                         224763 non-null  int64   
 6   price_range                         224763 non-null  category
 7   vegetarian_friendly                 224763 non-null  int64   
 8   vegan_options                       224763 non-null  int64   
 9   gluten_free                         224763 non-null  int64   
 10  open_days_per_week                  224763 non-null  float64 
 11  open_hours_pe

In [45]:
with open('df_after_feature_engineering.pkl', 'wb') as f:
    pickle.dump(df, f)

print("df_after_feature_engineering dataset saved as a pickle file.")

df_after_feature_engineering dataset saved as a pickle file.
